In [1]:
import os
import glob
import numpy as np
import pandas as pd
from math import log2
from tqdm import tqdm


In [16]:

# Function to calculate Chao-Shen entropy
def chao_shen(q):
    yx = q[q > 0]  # Remove bins with zero counts
    n = np.sum(yx)  # Total count
    p = yx.astype(float) / n  # Observed probabilities
    f1 = np.sum(yx == 1)  # Number of singletons in the sample

    if f1 == n:  # Avoid division by zero when all are singletons
        f1 -= 1

    C = 1 - (f1 / n)  # Estimated sample coverage
    pa = C * p  # Coverage-adjusted probabilities
    la = 1 - (1 - pa) ** n  # Probability of observing each category

    H = -np.sum((pa * np.log2(pa)) / la)  # Chao-Shen entropy

    return H, pa, la

# Function to calculate Chao-Shen transition entropy
def calculate_chao_shen_transition_entropy(raw_matrix, stationary_distribution):
    """
    Calculate entropy with Chao-Shen correction using the raw transition matrix counts.
    """
    total_entropy = 0
    category_entropies = {}

    for i, row in raw_matrix.iterrows():
        counts = row.values.astype(int)  # Use raw counts for Chao-Shen
        print(f"Raw counts for row {i}: {counts}")  # Debug raw counts
        if (counts.sum() > 1) & (len(row[row == 0.0]) < (len(row) - 1)):
            H, _, _ = chao_shen(counts)  # Apply Chao-Shen correction
            category_entropies[i] = H
            total_entropy += H * stationary_distribution.get(i, 0)  # Weighted by stationary distribution

    return total_entropy, category_entropies
# Function to calculate transition entropy
def calculate_transition_entropy(matrix, stationary_distribution):
    total_entropy = 0
    category_entropies = {}
    for i, row in matrix.iterrows():
        row_entropy = sum(-p * log2(p) for p in row if p > 0)
        category_entropies[i] = row_entropy
        total_entropy += row_entropy * stationary_distribution.get(i, 0)
    return total_entropy, category_entropies

# Define paths
input_dir = "/Volumes/TwoTeras/1_Experiment_2/Eye_Tracking/Pre_processed/05_Debbies_gaze/"
output_trials_dir = "/Volumes/TwoTeras/1_Experiment_2/Entropy_Results/Window/trials_df/"
output_transition_dir = "/Volumes/TwoTeras/1_Experiment_2/Entropy_Results/Window/transition_matrix/"
output_entropy_dir = "/Volumes/TwoTeras/1_Experiment_2/Entropy_Results/Window/entropy_results/"

# Ensure output directories exist
os.makedirs(output_trials_dir, exist_ok=True)
os.makedirs(output_transition_dir, exist_ok=True)
os.makedirs(output_entropy_dir, exist_ok=True)

# Mapping dictionary
mapping = {
    "TaskBuilding_Public": "Task_Building",
    "TaskBuilding_Residential": "Task_Building",
    "Active_Agent": "Agent",
    "Passive_Agent": "Agent",
    "Active_Agent_Face": "Agent",
    "Passive_Agent_Face": "Agent"
}

# Collider list
collider_list = [
    '56_Sa', '39_Sa', '19_Cma', '55_Sa', '25_Cma', '40_Sa', '41_Sa',
    '17_Cma', '47_Sa', '03_Cma', '13_Cma', '24_Cma', '01_Cma', '54_Sa',
    '15_Cma', '29_Sa', '04_Cma', '49_Sa', '30_Sa', '02_Cma', '51_Sa',
    '08_Cma', '28_Cma', '26_Cma', '44_Sa', '06_Cma', '53_Sa', '37_Sa',
    '32_Sa', '20_Cma', '16_Cma', '50_Sa', '34_Sa', '11_Cma', '38_Sa',
    '33_Sa', '12_Cma', '22_Cma', '42_Sa', '05_Cma', '23_Cma', '18_Cma',
    '27_Cma', '45_Sa', '43_Sa', '09_Cma', '31_Sa', '48_Sa', '10_Cma',
    '52_Sa', '07_Cma', '46_Sa', '35_Sa', '36_Sa', '21_Cma', '14_Cma'
]

# Get list of files to process
file_paths = glob.glob(os.path.join(input_dir, "*.csv"))

# Process all CSV files
for file_path in tqdm(file_paths, desc="Processing Files", unit="file"):
    # Load the data
    data = pd.read_csv(file_path)
    data['date_seconds'] = pd.to_datetime(data['timeStampDataPointEnd'], unit='s')

    # Filter for the desired gaze events
    data_Reduced = data[data['events'] == -2]

    # Filter and label rows with colliders
    filtered_df = data_Reduced[data_Reduced['names'].isin(collider_list)].copy()
    filtered_df['Occurrence_Order'] = filtered_df.groupby('names').cumcount() + 1

    # Segment data by each occurrence of colliders
    last_processed_time = {}
    trials = []
    for index, row in filtered_df.iterrows():
        collider_name = row['names']
        occurrence_time = row['date_seconds']

        if collider_name in last_processed_time and (occurrence_time - last_processed_time[collider_name]).total_seconds() <= 50:
            continue

        last_processed_time[collider_name] = occurrence_time

        window_start = max(data_Reduced['date_seconds'].min(), occurrence_time - pd.Timedelta(seconds=5))
        window_end = min(data_Reduced['date_seconds'].max(), occurrence_time + pd.Timedelta(seconds=55))

        trial_segment = data_Reduced[
            (data_Reduced['date_seconds'] >= window_start) &
            (data_Reduced['date_seconds'] <= window_end)
        ].copy()

        trial_segment['Collider_Name'] = collider_name
        trial_segment['Occurrence_Order'] = len(trials) + 1
        trial_segment['Trial_ID'] = f"{collider_name}_Trial_{len(trials) + 1}"
        trials.append(trial_segment)

    if trials:
        trials_df = pd.concat(trials, ignore_index=True)
        trials_df.to_csv(os.path.join(output_trials_dir, f"{os.path.basename(file_path).replace('.csv', '_trials.csv')}"), index=False)
    else:
        print(f"No trials found for file: {file_path}")
        continue

    # Calculate entropy for each trial
    entropy_results = []
    for trial_id, trial_data in trials_df.groupby('Trial_ID'):
        collider_name = trial_data['Collider_Name'].iloc[0]
        occurrence_order = trial_data['Occurrence_Order'].iloc[0]

        trial_data["Mapped_Column_Collider_Categorical"] = trial_data["Collider_CategoricalN"].replace(mapping)
        gaze_sequence = trial_data['Mapped_Column_Collider_Categorical'].reset_index(drop=True)

    
        categories = gaze_sequence.unique()
        raw_transition_matrix = pd.DataFrame(0, index=categories, columns=categories, dtype=float)

        for i in range(len(gaze_sequence) - 1):
            current_category = gaze_sequence.iloc[i]
            next_category = gaze_sequence.iloc[i + 1]
            raw_transition_matrix.loc[current_category, next_category] += 1

        print(f"Raw transition matrix for trial {trial_id}:\n{raw_transition_matrix}")

        transition_matrix = raw_transition_matrix.div(raw_transition_matrix.sum(axis=1), axis=0).fillna(0)

        try:
            eigvals, eigvecs = np.linalg.eig(transition_matrix.T)
            stationary_distribution = np.real(eigvecs[:, np.isclose(eigvals, 1)].flatten())
            stationary_distribution /= stationary_distribution.sum()
            stationary_distribution_dict = {categories[i]: stationary_distribution[i] for i in range(len(categories))}
        except:
            stationary_distribution_dict = {category: 1 / len(categories) for category in categories}

        print(f"Stationary distribution for trial {trial_id}: {stationary_distribution_dict}")

        overall_transition_entropy, transition_entropy_per_category = calculate_chao_shen_transition_entropy(
            raw_transition_matrix, stationary_distribution_dict
        )

        num_categories = len(categories)
        normalized_overall_entropy = overall_transition_entropy / log2(num_categories) if num_categories > 1 else 0
        print(f"Chao Shen trial", overall_transition_entropy, transition_entropy_per_category)
        result = {
            'Trial_ID': trial_id,
            'Collider_Name': collider_name,
            'Occurrence_Order': occurrence_order,
            'Gaze_Sequence_Length': len(gaze_sequence),
            'Chao_Shen_Overall_Transition_Entropy': overall_transition_entropy
        }

        for category in categories:
            result[f'Chao_Shen_Transition_Entropy_{category}'] = transition_entropy_per_category.get(category, 0)

        entropy_results.append(result)

    participant_id = file_path[-10:-4]
    entropy_df = pd.DataFrame(entropy_results)


Processing Files:   0%|                               | 0/144 [00:00<?, ?file/s]

Raw transition matrix for trial 01_Cma_Trial_22:
               Task_Building  Background  Building  Agent
Task_Building           29.0         9.0       7.0    5.0
Background              11.0        71.0      14.0    3.0
Building                 4.0        16.0      22.0    2.0
Agent                    5.0         4.0       1.0   13.0
Stationary distribution for trial 01_Cma_Trial_22: {'Task_Building': 0.2224878278461625, 'Background': 0.468442947394564, 'Building': 0.20392820369536774, 'Agent': 0.10514102106390578}
Raw counts for row Task_Building: [29  9  7  5]
Raw counts for row Background: [11 71 14  3]
Raw counts for row Building: [ 4 16 22  2]
Raw counts for row Agent: [ 5  4  1 13]
Chao Shen trial 1.452531965790698 {'Task_Building': 1.6323718701209482, 'Background': 1.2557387987084438, 'Building': 1.5827742766560646, 'Agent': 1.6961485940251388}
Raw transition matrix for trial 03_Cma_Trial_16:
               Background  Task_Building  Agent  Building
Background          124.0 

Raw transition matrix for trial 28_Cma_Trial_5:
                 Background  Global_Landmark  Agent  Building  Task_Building
Background            135.0              1.0    6.0      10.0            4.0
Global_Landmark         2.0              3.0    0.0       0.0            0.0
Agent                   5.0              1.0    8.0       0.0            0.0
Building               10.0              0.0    0.0      18.0            0.0
Task_Building           4.0              0.0    0.0       0.0            2.0
Stationary distribution for trial 28_Cma_Trial_5: {'Background': 0.7464114832535889, 'Global_Landmark': 0.023923444976076375, 'Agent': 0.06698564593301434, 'Building': 0.13397129186602866, 'Task_Building': 0.028708133971291832}
Raw counts for row Background: [135   1   6  10   4]
Raw counts for row Global_Landmark: [2 3 0 0 0]
Raw counts for row Agent: [5 1 8 0 0]
Raw counts for row Building: [10  0  0 18  0]
Raw counts for row Task_Building: [4 0 0 0 2]
Chao Shen trial 0.8952008189186

Processing Files:   1%|▏                      | 1/144 [00:02<06:46,  2.85s/file]

Raw transition matrix for trial 54_Sa_Trial_3:
                 Background  Task_Building  Building  Agent  Global_Landmark
Background            102.0            5.0      11.0    0.0              7.0
Task_Building           3.0           32.0       2.0    5.0              0.0
Building               13.0            2.0      14.0    1.0              0.0
Agent                   1.0            3.0       2.0    6.0              0.0
Global_Landmark         6.0            0.0       1.0    0.0             10.0
Stationary distribution for trial 54_Sa_Trial_3: {'Background': 0.5530973451327433, 'Task_Building': 0.18584070796460195, 'Building': 0.13274336283185828, 'Agent': 0.05309734513274337, 'Global_Landmark': 0.07522123893805314}
Raw counts for row Background: [102   5  11   0   7]
Raw counts for row Task_Building: [ 3 32  2  5  0]
Raw counts for row Building: [13  2 14  1  0]
Raw counts for row Agent: [1 3 2 6 0]
Raw counts for row Global_Landmark: [ 6  0  1  0 10]
Chao Shen trial 1.1760009

...

Raw transition matrix for trial 08_Cma_Trial_6:
                 Building  Background  Task_Building  Agent  Global_Landmark
Building             25.0        19.0            0.0    0.0              2.0
Background           20.0       104.0            2.0    0.0              0.0
Task_Building         1.0         1.0            7.0    1.0              0.0
Agent                 0.0         0.0            1.0    0.0              0.0
Global_Landmark       0.0         2.0            0.0    0.0              1.0
Stationary distribution for trial 08_Cma_Trial_6: {'Building': 0.24731182795698922, 'Background': 0.6774193548387099, 'Task_Building': 0.05376344086021508, 'Agent': 0.005376344086021512, 'Global_Landmark': 0.016129032258064512}
Raw counts for row Building: [25 19  0  0  2]
Raw counts for row Background: [ 20 104   2   0   0]
Raw counts for row Task_Building: [1 1 7 1 0]
Raw counts for row Agent: [0 0 1 0 0]
Raw counts for row Global_Landmark: [0 2 0 0 1]
Chao Shen trial 0.9547748311452

Raw transition matrix for trial 23_Cma_Trial_34:
               Task_Building  Building  Background  Agent
Task_Building            3.0       1.0         1.0    0.0
Building                 1.0       5.0         6.0    0.0
Background               0.0       6.0        32.0    1.0
Agent                    0.0       0.0         1.0    0.0
Stationary distribution for trial 23_Cma_Trial_34: {'Task_Building': 0.04322766570605223, 'Building': 0.20749279538904883, 'Background': 0.7305475504322765, 'Agent': 0.018731988472622474}
Raw counts for row Task_Building: [3 1 1 0]
Raw counts for row Building: [1 5 6 0]
Raw counts for row Background: [ 0  6 32  1]
Raw counts for row Agent: [0 0 1 0]
Chao Shen trial 1.0499086522601637 {'Task_Building': 2.148929832066702, 'Building': 1.5093561791025258, 'Background': 0.8813045757707861}
Raw transition matrix for trial 25_Cma_Trial_35:
                 Building  Background  Task_Building  Agent  Global_Landmark
Building             17.0        17.0        

Raw transition matrix for trial 46_Sa_Trial_10:
               Task_Building  Building  Background  Agent
Task_Building            9.0       4.0         8.0    1.0
Building                 3.0      39.0        22.0    1.0
Background               9.0      22.0        86.0    1.0
Agent                    0.0       0.0         3.0    3.0
Stationary distribution for trial 46_Sa_Trial_10: {'Task_Building': 0.09721035732170746, 'Building': 0.3082746634459599, 'Background': 0.5665890947653693, 'Agent': 0.02792588446696326}
Raw counts for row Task_Building: [9 4 8 1]
Raw counts for row Building: [ 3 39 22  1]
Raw counts for row Background: [ 9 22 86  1]
Raw counts for row Agent: [0 0 3 3]
Chao Shen trial 1.27565009971365 {'Task_Building': 1.8200741539925502, 'Building': 1.3354554016898665, 'Background': 1.1625070619253295, 'Agent': 1.0158730158730158}
Raw transition matrix for trial 47_Sa_Trial_30:
               Background  Building  Task_Building  Agent
Background           67.0      14.0  

Processing Files: 100%|█████████████████████| 144/144 [07:36<00:00,  3.17s/file]

Raw transition matrix for trial 56_Sa_Trial_14:
               Background  Building  Agent  Task_Building
Background           90.0      15.0    2.0            5.0
Building             16.0      25.0    0.0            2.0
Agent                 1.0       1.0    7.0            2.0
Task_Building         5.0       2.0    2.0           13.0
Stationary distribution for trial 56_Sa_Trial_14: {'Background': 0.5957446808510639, 'Building': 0.22872340425531884, 'Agent': 0.05851063829787224, 'Task_Building': 0.11702127659574499}
Raw counts for row Background: [90 15  2  5]
Raw counts for row Building: [16 25  0  2]
Raw counts for row Agent: [1 1 7 2]
Raw counts for row Task_Building: [ 5  2  2 13]
Chao Shen trial 1.1611561602392764 {'Background': 0.9630342792275112, 'Building': 1.221953348789052, 'Agent': 1.956955467811357, 'Task_Building': 1.6530461230749336}


In [7]:
df = pd.DataFrame(
    data=[
        [45.0, 21.0, 2.0, 0.0],  # Background
        [17.0, 42.0, 7.0, 1.0],  # Building
        [5.0, 5.0, 26.0, 4.0],   # Task_Building
        [0.0, 0.0, 5.0, 0.0]     # Agent
    ],
    index=["Background", "Building", "Task_Building", "Agent"],
    columns=["Background", "Building", "Task_Building", "Agent"]
)


In [17]:
entropy_df.head()

Trial_ID Collider_Name  Occurrence_Order  Gaze_Sequence_Length  \
0  02_Cma_Trial_27        02_Cma                27                   175   
1  02_Cma_Trial_40        02_Cma                40                   192   
2  03_Cma_Trial_41        03_Cma                41                   180   
3  05_Cma_Trial_33        05_Cma                33                    97   
4  06_Cma_Trial_42        06_Cma                42                   182   

   Chao_Shen_Overall_Transition_Entropy  \
0                              1.184827   
1                              0.672946   
2                              1.196369   
3                              1.162549   
4                              1.019216   

   Chao_Shen_Transition_Entropy_Background  \
0                                 1.128815   
1                                 0.550318   
2                                 1.102924   
3                                 0.938490   
4                                 0.852676   

   Chao_Shen_Transition_Entropy_Task_Building  \
0                                    1.312855   
1                                    2.543818   
2                                    1.840111   
3                                    1.589459   
4                                    2.628756   

   Chao_Shen_Transition_Entropy_Agent  Chao_Shen_Transition_Entropy_Building  \
0                            2.242256                               0.970952   
1                            1.066667                               3.292302   
2                            1.538270                               1.339273   
3                            3.549732                               1.427068   
4                            0.000000                               1.249806   

   Chao_Shen_Transition_Entropy_Global_Landmark  
0                                           NaN  
1                                      0.820271  
2                                      0.000000  
3                                           NaN  
4                                      2.285714

In [9]:
for i, row in df.iterrows():
   
    counts = row.values.astype(int) 
    if counts.sum() > 1:
        H, _, _ = chao_shen(counts)
        print(H)
            

1.0899086383828307
1.4095052980025744
1.4947537009368297
-0.0


In [13]:
len(row[row == 0.0])

3

In [6]:
# Function to calculate Chao-Shen entropy
def chao_shen(q):
    yx = q[q > 0]  # Remove bins with zero counts
    n = np.sum(yx)  # Total count
    p = yx.astype(float) / n  # Observed probabilities
    f1 = np.sum(yx == 1)  # Number of singletons in the sample

    if f1 == n:  # Avoid division by zero when all are singletons
        f1 -= 1

    C = 1 - (f1 / n)  # Estimated sample coverage
    pa = C * p  # Coverage-adjusted probabilities
    la = 1 - (1 - pa) ** n  # Probability of observing each category

    H = -np.sum((pa * np.log2(pa)) / la)  # Chao-Shen entropy

    return H, pa, la

# Function to calculate Chao-Shen transition entropy
def calculate_chao_shen_transition_entropy(raw_matrix, stationary_distribution):
    """
    Calculate entropy with Chao-Shen correction using the raw transition matrix counts.
    """
    total_entropy = 0
    category_entropies = {}

    for i, row in raw_matrix.iterrows():
        counts = row.values.astype(int)  # Use raw counts for Chao-Shen
        print(f"Raw counts for row {i}: {counts}")  # Debug raw counts
        if counts.sum() > 0:
            H, _, _ = chao_shen(counts)  # Apply Chao-Shen correction
            category_entropies[i] = H
            total_entropy += H * stationary_distribution.get(i, 0)  # Weighted by stationary distribution

    return total_entropy, category_entropies